<img id="top" style="float:left;height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:100px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center></center>

<center>
<h3 style="color:#888888;"> <i>--  Simulation numérique en mécanique des fluides  --</i> </h3>
<h1> TP n°7 </h1>
<h3> Résolution numérique de l'équation de diffusion</h3>
<h4> TP à rendre </h4>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</center>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import copy
# la librairie time nous sera utile pour calculer le temps d'execution des scripts
import time 
#Option pour afficher les figures dans le notebook et eviter le plt.show():
%matplotlib inline   

On se propose dans ce TP d'étudier la résolution numérique d'un problème parabolique type, l'équation de diffusion instationnaire.

L'équation de diffusion est donnée par:

$$
\displaystyle{\dfrac{\partial f}{\partial t}=\nu\dfrac{\partial^2 f}{\partial x^2}}
$$

Cette équation modélise la diffusion isotrope d'une quantité $f$ en fonction du temps (en mécanique des fluides cette quantité peut être la quantité de mouvement ou la température par exemple).

L'objectif de se TP est d'étudier la résolution numérique de cette équation à l'aide d'une approche explicite, puis implicite en temps et d'étudier leur condition de stabilité.

<h1>1 - Initialisation</h1>

On prendra comme domaine de calcul le segment $[-1, 1]$. Pour l'initialisation on va choisir une fonction impulsion qui vaut $0$ partout sauf au centre du domaine. (Cette condition initiale correspond par exemple à l'introduction d'un composant chimique dans un fluide au temps $t_0$, l'équation de diffusion regarde alors l'évolution de sa concentration en fonction du temps).

<b>En complétant le block suivant,tracer la condition initiale</b>

In [ ]:
def init(dx):
    x=...
    f0=...
    return x,f0

x,f0=init(2e-2)
plt.plot(x,f0)

<h1>2 - Approche Explicite</h1>

La forme discrète de l'équation de diffusion en utilisant le schéma d'Euler explicite et un schéma centré d'ordre 2 pour l'espace s'écrit:

$$
\dfrac{f^{n+1}_{j}-f^{n}_{j}}{\Delta t}=\nu
\left(\dfrac{f^{n}_{j+1}-2f^{n}_{j}+f^{n}_{j-1}}{\Delta x^2}\right)
$$

ce qui donne pour la mise à jour de $f^{n+1}_{j}$:

$$
\displaystyle{f^{n+1}_{j}=f^{n}_{j}+\nu\dfrac{\Delta t}{\Delta x^2} (f^{n}_{j-1}+f^{n}_{j+1}-2f^{n}_j)}
$$

Dans la suite on posera $\lambda=\nu\dfrac{\Delta t}{\Delta x^2}$

<b> Proposer une fonction qui résout numériquement cette équation et qui enregistre l'évolution de f au centre du domaine. On veillera en particulier à utiliser du slicing pour la boucle spatiale (voir notebook d'intro Python)</b>

In [ ]:
def Solv_diff_exp(dx,T,C):
    ### Attention ici C represente Lambda !! ######
    x,f0=init(dx)
    ...
    ...
    ...
    for t in xrange(nt):
        f=f0.copy()
        ...
        ...
    t=time.time()-t0
    return x,f0,fcenter,t    


<b>Représenter la solution numérique pour un temps physique de simulation de 2 secondes, un pas d'espace de $\Delta x=2$cm et différentes valeurs de $\lambda$</b>

In [ ]:
x,f0,fc,t=Solv_diff_exp(2e-2,2,0.4);plt.plot(x,f0)
x,f0,fc,t=Solv_diff_exp(2e-2,2,0.2);plt.plot(x,f0)
x,f0,fc,t=Solv_diff_exp(2e-2,2,0.1);plt.plot(x,f0)

<b>Comparer l'évolution des solutions au centre du domaine en fonctions du temps.</b>

Discussions:

<b>Augmenter le CFL au delà de 0.5. Relier vos observations aux résultats du cours.</b>

Discussions:

<h1>3 - Approche Implicite avec Crank-Nicholson</h1>

Pour l'implicitation temporelle on utilise souvent le schéma de Crank-Nicholson dans le cadre de la résolution de l'équation de diffusion. Ce schéma consiste à faire la moyenne temporelle entre deux itérations succéssive du schéma d'euler. Pour l'espace on gardera ici le schéma centré d'ordre 2. Ce qui donne pour l'équation discrète:

$$
\displaystyle{f^{n+1}_{j}=f^{n}_{j}+\nu\dfrac{\Delta t}{\Delta x^2} \left(\dfrac{f^{n}_{j-1}+f^{n}_{j+1}-2f^{n}_j}{2} + \dfrac{f^{n+1}_{j-1}+f^{n+1}_{j+1}-2f^{n+1}_j}{2}\right)}
$$

en posant $\lambda=\nu\dfrac{\Delta t}{\Delta x^2}$ et en séparant les termes en $n+1$ des termes en $n$, on peut réécrire l'équation discrète sous la forme:

$$
\displaystyle{2(1+\lambda)f^{n+1}_{j}-\lambda f^{n+1}_{j-1}-\lambda f^{n+1}_{j+1}=2(1-\lambda)f^{n}_{j}+\lambda f^{n}_{j-1}+\lambda f^{n}_{j+1}}
$$

que l'on peut écrire sous la forme matricielle:
$$
\mathbf{A} \mathbf{f}^{n+1}=\mathbf{B}\mathbf{f}^n
$$

avec, 
 $$
A= \left[
 \begin{array}{ccccc}
  2(1+\lambda)&-\lambda&0 &\cdots&0\\
  -\lambda&2(1+\lambda)&-\lambda & \ddots&\vdots\\
  0&\ddots&\ddots &\ddots&0\\
  \vdots&\ddots&-\lambda &2(1+\lambda)&-\lambda\\
  0&\cdots&0 &-\lambda&2(1+\lambda)
 \end{array}
\right]
 $$
 
 et
 
  $$
B= \left[
 \begin{array}{ccccc}
  2(1-\lambda)&\lambda&0 &\cdots&0\\
  \lambda&2(1-\lambda)&\lambda & \ddots&\vdots\\
  0&\ddots&\ddots &\ddots&0\\
  \vdots&\ddots&\lambda &2(1-\lambda)&\lambda\\
  0&\cdots&0 &\lambda&2(1-\lambda)
 \end{array}
\right]
 $$

<b>Proposer une fonction permettant de résoudre l'équation de diffusion avec le schéma de Crank-Nicholson</b>

In [ ]:
def Solv_diff_imp(dx,T,C):
    x,f0=init(dx)
    Nt=...
    A=...
    B=...
    f=...
    t=time.time()-t0
    print Nt,t
    return x,f


<b>En prenant les mêmes paramètres que pour la version explicite, comparer les solutions issues du calcul explicite avec celles issues du calcul implicite.</b>

In [ ]:
x,f=Solv_diff_imp(2e-2,2,0.2);plt.plot(x,f)
x,f=Solv_diff_exp(2e-2,2,0.2);plt.plot(x,f)

<b>Augmenter le CFL au delà de 0.5 et commenter les résultats.</b>

Discussions

# Conclusion

Présentez une synthèse de vos résultats et des étapes de calcul de votre TP.


In [1]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<img id="top" style="float:right;height:100px;" src="https://hpp.education/Lessons/omnes-docet-ubique.png"/>
<a style="float:left;" href="http://www.cnam.fr//"><img style="height:100px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center><a href="#top">Retour en haut de la page</a></center>